In [1]:
import os
import sys
import cv2
import ntpath
import random
import math
import numpy as np
import skimage.io
import matplotlib
import matplotlib.pyplot as plt
import collections
import struct
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
import glob
import read_model

In [2]:
def video_to_frames(video_file):
    vidcap = cv2.VideoCapture(video_file)
    video_name = ((ntpath.basename(video_file)).split("."))[0]
    os.system("mkdir data/projects/" + video_name)
    os.system("mkdir data/projects/" + video_name + "/images")
    success,image = vidcap.read()
    count = 1
    project_dir = os.getcwd() + "/data/projects/" + video_name + "/"
    while success:
        cv2.imwrite(project_dir + "images/" + video_name + "_frame_%d.jpg" % count, image)     # save frame as JPEG file      
        vidcap.set(cv2.CAP_PROP_POS_MSEC,(count*100))
        success,image = vidcap.read()
        print('Read a new frame #' + str(count) + ': ', success)
        count += 1  
        if count > 0:
            break 
    print("Obtained " + str(count-1) + " images")
    return project_dir

In [3]:
def plot_points3D(points3D):
    fig = plt.figure()
    ax = fig.add_subplot(111, projection='3d')

    i = 0;
    X = [];
    Y = [];
    Z = [];
    n_points = len(points3D)
    #n_points = 100
    RGB = np.zeros(shape=(n_points,3));

    for point_id in points3D:
        if i >= n_points:
            break
        point = points3D[point_id]
        xyz = point.xyz
        rgb = point.rgb  

        X.append(xyz[0])
        Y.append(xyz[1])
        Z.append(xyz[2])
        RGB[i, :] = rgb/256
        i = i+1

    Xmean = np.mean(X)
    Xstd = np.std(X)
    Ymean = np.mean(Y)
    Ystd = np.std(Y)
    Zmean = np.mean(Z)
    Zstd = np.std(Z)

    ax.scatter(X, Y, Z, facecolors = RGB, s=1)

    ax.set_xlabel('X Label')
    ax.set_ylabel('Y Label')
    ax.set_zlabel('Z Label')

    t_n = 2.5
    ax.set_xlim([Xmean - t_n*Xstd, Xmean + t_n*Xstd])
    ax.set_ylim([Ymean - t_n*Ystd, Ymean + t_n*Ystd])
    ax.set_zlim([Zmean - t_n*Zstd, Zmean + t_n*Zstd])

    plt.show()
    return

In [101]:
class_names = ['BG', 'person', 'bicycle', 'car', 'motorcycle', 'airplane',
               'bus', 'train', 'truck', 'boat', 'traffic light',
               'fire hydrant', 'stop sign', 'parking meter', 'bench', 'bird',
               'cat', 'dog', 'horse', 'sheep', 'cow', 'elephant', 'bear',
               'zebra', 'giraffe', 'backpack', 'umbrella', 'handbag', 'tie',
               'suitcase', 'frisbee', 'skis', 'snowboard', 'sports ball',
               'kite', 'baseball bat', 'baseball glove', 'skateboard',
               'surfboard', 'tennis racket', 'bottle', 'wine glass', 'cup',
               'fork', 'knife', 'spoon', 'bowl', 'banana', 'apple',
               'sandwich', 'orange', 'broccoli', 'carrot', 'hot dog', 'pizza',
               'donut', 'cake', 'chair', 'couch', 'potted plant', 'bed',
               'dining table', 'toilet', 'tv', 'laptop', 'mouse', 'remote',
               'keyboard', 'cell phone', 'microwave', 'oven', 'toaster',
               'sink', 'refrigerator', 'book', 'clock', 'vase', 'scissors',
               'teddy bear', 'hair drier', 'toothbrush']

In [4]:
def label_points(IMAGE_DIR):
    # Root directory of the project
    ROOT_DIR = os.getcwd()
    # Import Mask RCNN
    sys.path.append(os.path.join(ROOT_DIR, "code/"))  # To find local version of the library
    from mrcnn import utils
    import mrcnn.model as modellib
    from mrcnn import visualize
    # Import COCO config
    sys.path.append(os.path.join(ROOT_DIR, "code/coco/"))  # To find local version
    import coco
    # Directory to save logs and trained model
    MODEL_DIR = os.path.join(ROOT_DIR, "logs/")
    # Local path to trained weights file
    COCO_MODEL_PATH = os.path.join(ROOT_DIR, "MASK_RCNN_models/mask_rcnn_coco.h5")
    # Download COCO trained weights from Releases if needed
    if not os.path.exists(COCO_MODEL_PATH):
        #raise Exception("Can not find COCO_MODELL")
        utils.download_trained_weights(COCO_MODEL_PATH)

    # Directory of images to run detection on
    class InferenceConfig(coco.CocoConfig):
        # Set batch size to 1 since we'll be running inference on
        # one image at a time. Batch size = GPU_COUNT * IMAGES_PER_GPU
        GPU_COUNT = 1
        IMAGES_PER_GPU = 1

    config = InferenceConfig()
    # config.display()

    # Create model object in inference mode.
    model = modellib.MaskRCNN(mode="inference", model_dir=MODEL_DIR, config=config)
    # Load weights trained on MS-COCO
    model.load_weights(COCO_MODEL_PATH, by_name=True)

    # COCO Class names
    # Index of the class in the list is its ID. For example, to get ID of
    # the teddy bear class, use: class_names.index('teddy bear')



    # Object Detection
    labeled_points = []
    count = 1
    for image_file in glob.glob(IMAGE_DIR + "*.jpg"):
#         if count > 1:
#             break
        print("Processing image # " + str(count))
        count += 1
        image = skimage.io.imread(image_file)

        # Run detection
        results = (model.detect([image], verbose=1))[0]
        labeled_points.append(results)
        # Visualize results
        # visualize.display_instances(image, results['rois'], results['masks'], results['class_ids'], class_names, results['scores'])
    return labeled_points


In [5]:
def combine(labeled_points, cameras, images, points3D):
    images_n = len(images)
    points3D_n = len(max(points3D))

    points3D_on_images = np.zeros((points3D_n,images_n))

    images_n = len(labeled_points)
    for i in range(images_n):
        labeled_point = labeled_points[i]
        masks = labeled_point['masks']
        masks = masks.astype(int)   
        masks_n = len(masks[0,0,:])
        masks_1 = len(masks[:,0,0])
        masks_2 = len(masks[0,:,0])
        for j in range(masks_n):
            masks[:, :, j] = (j+1)*masks[:, :, j]
        points2D_n = len(images[i+1].point3D_ids)
        for j in range(points2D_n):
            point3D_id = images[i+1].point3D_ids[j]
            if (point3D_id == -1):
                continue 
            xy = images[i+1].xys[j]
            x = round(xy[0])
            y = round(xy[1])

    return points3D_on_images

In [6]:
home = os.path.expanduser("~") + "/"
os.chdir(home+"Documents/Projects/Others/distances/")
video_file = "/Users/ukhatov/Documents/Projects/Others/distances/data/videos/20190530_185852.mp4"
project_dir = video_to_frames(video_file)

Read a new frame #1:  True
Obtained 1 images


In [7]:
# os.system("colmap automatic_reconstructor --workspace_path " + project_dir + " --image_path " + project_dir + "images/")
# os.system("colmap feature_extractor  --database_path " + project_dir + "/database.db --image_path " + project_dir + "/images")
cameras, images, points3D = read_model.read_model(path=project_dir+"sparse/0/", ext=".bin")

In [8]:
#plot_points3D(points3D)
labeled_points = label_points(project_dir + "images/")

Instructions for updating:
Colocations handled automatically by placer.


Using TensorFlow backend.


Instructions for updating:
Use tf.cast instead.
Processing image # 1
Processing 1 images
image                    shape: (1080, 1920, 3)       min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1920.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing image # 2
Processing 1 images
image                    shape: (1080, 1920, 3)       min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  150.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1920.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing image # 3
Processing 1 images
image                    shape: (1080, 1920, 3)       min:    0.0

Processing image # 20
Processing 1 images
image                    shape: (1080, 1920, 3)       min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1920.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing image # 21
Processing 1 images
image                    shape: (1080, 1920, 3)       min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1920.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing image # 22
Processing 1 images
image                    shape: (1080, 1920, 3)       min:    0.00000  max:  255.00000  uint8
molded_images   

In [9]:
#points3D_on_images = utils.combine(labeled_points, cameras, images, points3D)

In [134]:
images_n = len(images)
points3D_n = max(points3D)
points3D_on_images = np.zeros((points3D_n,images_n+2))
points3D_on_images_classes = -np.ones((points3D_n,images_n))

images_n = len(labeled_points)
for i in range(images_n):
    labeled_point = labeled_points[i]
    masks = labeled_point['masks']
    class_ids = labeled_point['class_ids']
    masks = masks.astype(int)   
    masks_n = len(masks[0,0,:])
    masks_1 = len(masks[:,0,0])
    masks_2 = len(masks[0,:,0])
    mask = masks[:, :, 0]
    for j in range(masks_n):
        #masks[:, :, j] = (j+1)*masks[:, :, j]
        mask = mask + np.logical_xor(mask, masks[:, :, j]*((j+1)*masks[:, :, j]))
    points2D_n = len(images[i+1].point3D_ids)
    for j in range(points2D_n):
        point3D_id = images[i+1].point3D_ids[j]
        if (point3D_id == -1):
            continue 
        xy = images[i+1].xys[j]
        x = int(round(xy[0]))
        y = int(round(xy[1]))
        points3D_on_images[point3D_id-1][i+1] = mask[y][x]
        if mask[y][x] != 0:
            points3D_on_images_classes[point3D_id-1][i] = class_ids[mask[y][x]-1]
        if points3D_on_images[point3D_id-1][images_n+1] == 0:
            points3D_on_images[point3D_id-1][images_n+1] = point3D_id



In [135]:
points3D_on_images = points3D_on_images[~np.all(points3D_on_images == 0, axis=1)]
points3D_on_images = points3D_on_images.astype(int)
points3D_on_images_classes = 1+points3D_on_images_classes.astype(int)
for i in range(len(points3D_on_images)):
    counts = np.bincount(points3D_on_images_classes[i])
    counts[0] = 0
    points3D_on_images[i][0] = np.argmax(counts)-1
    if len(counts) == 0:
        points3D_on_images[i][0] = -1
points3D_on_images = points3D_on_images[(points3D_on_images[:, 0] != -1)]
#return points3D_on_images

In [158]:
from sklearn.cluster import KMeans

clf = KMeans(n_clusters=3)
clf.fit(points3D_on_images[:, 1:images_n])
print(clf.cluster_centers_)
clusters = clf.fit_predict(points3D_on_images[:, 1:images_n])
print(clusters)

[[1.25298900e-01 1.20038259e-01 2.09469154e-01 1.61429938e+00
  1.08799617e+00 1.50167384e-01 6.52797704e-02 9.13438546e-02
  8.84744142e-02 6.33668101e-02 1.35820182e-01 2.54423721e-01
  3.13247250e-02 3.56288857e-02 7.46054519e-02 5.67670971e-01
  2.72596844e-02 2.65423242e-02 5.18890483e-02 4.37589670e-02
  3.41941655e-02 6.69536107e-02 5.42802487e-02 7.06121473e-01
  3.20420851e-02 2.19033955e-01 3.81874701e-01 1.85318030e+00
  1.83907221e+00 6.25777140e-01]
 [7.98294904e-02 8.87424918e-02 1.56558806e-01 3.87521798e-04
  3.77833753e-03 1.49680295e-01 7.40166634e-02 1.44933152e-01
  1.45223794e-01 8.87424918e-02 1.66537493e-01 4.19104825e-01
  1.75256733e-01 1.30013563e-01 1.79906995e-01 2.86766131e-02
  3.25227669e-01 1.28269715e-01 2.85603565e-01 2.87056772e-01
  8.30265452e-02 3.59135826e-01 2.49564038e-01 5.28967254e-02
  1.60627785e-01 1.10443712e-01 1.24685139e-01 8.55454369e-02
  1.08602984e-01 1.05502810e-01]
 [3.64082434e-01 5.08832188e-01 9.89205103e-01 7.25711482e-01
  5.

In [159]:
for i, a in enumerate(points3D_on_images):
#     if not (a[0] == 29 and clusters[i]==0):
    print(class_names[a[0]])
    print(a)
    print(clusters[i])

suitcase
[29  0  1  0  3  2  0  0  0  0  0  1  2  0  0  0  1  2  0  2  0  0  2  0
  1  0  0  0  0  2  1  1  1]
0
suitcase
[29  1  0  0  3  2  0  1  2  2  1  1  2  0  1  1  1  2  1  2  1  1  2  1
  1  1  0  1  2  2  1  1  2]
2
suitcase
[29  1  1  0  0  0  0  1  2  2  1  1  2  1  1  2  0  2  1  2  1  1  2  1
  0  1  1  1  0  2  1  1  6]
2
suitcase
[29  0  1  2  0  0  2  1  2  2  1  1  2  1  1  2  1  2  1  2  1  1  2  1
  0  0  1  1  2  2  1  1  8]
2
suitcase
[29  1  1  2  0  0  2  1  2  2  1  1  2  0  1  0  0  0  0  0  0  0  0  0
  0  0  1  0  2  2  0  1  9]
2
suitcase
[29  1  1  0  0  0  0  1  2  2  1  1  2  0  0  0  0  0  0  0  0  0  2  0
  1  0  1  1  2  2  1  1 10]
2
suitcase
[29  0  0  0  3  2  0  0  2  0  1  0  0  0  0  0  0  0  0  0  0  0  0  0
  1  0  0  0  0  2  1  1 11]
0
suitcase
[29  0  1  0  0  0  0  1  2  2  1  1  2  1  1  0  0  2  0  0  2  0  2  1
  0  1  0  0  2  2  0  1 13]
2
suitcase
[29  1  1  2  0  0  2  1  2  2  1  1  2  1  1  2  0  2  1  2  1  1  2  1
  1  1  1  1  

    0    0    0    0 1019]
1
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    1    0
    0    0    0    0    0    0    2    0    2    1    0    1    0    0
    0    0    0    0 1020]
1
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    2    0    2    1    0    1    0    0
    0    0    0    0 1021]
1
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    1    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 1024]
1
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    1    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 1025]
1
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    1    0
    0    0    0    0    0    0    2    0    2    1    0    1    0    0
    0    0    0    0 1027]
1
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0  

[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    2    0    2    1    0    1    0    0
    0    0    0    0 2245]
1
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    1    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 2247]
1
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    2    0    2    1    0    1    0    0
    0    0    0    0 2248]
1
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    2    0    2    1    0    1    0    0
    0    0    0    0 2249]
1
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    1    0
    0    0    0    0    0    0    2    0    2    1    0    1    0    0
    0    0    0    0 2251]
1
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    1    0
    0    0    0    0    0    

2
suitcase
[  29    0    1    0    0    0    2    1    2    2    1    1    2    1
    1    2    0    2    0    2    1    1    0    1    0    0    0    0
    0    0    0    0 5734]
2
suitcase
[  29    0    0    0    0    0    2    1    2    2    1    0    2    0
    1    2    0    0    0    0    1    1    0    0    0    0    0    0
    0    0    0    0 5746]
2
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    1    2    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 5767]
1
handbag
[  27    1    1    2    0    0    1    1    2    2    1    1    2    1
    1    2    1    2    1    2    1    1    0    1    1    1    1    1
    2    2    1    1 5789]
2
suitcase
[  29    0    1    2    0    0    2    1    2    2    1    1    2    0
    1    0    0    0    1    0    1    0    0    1    1    1    1    1
    2    2    1    1 5795]
2
suitcase
[  29    1    1    2    0    0    1    1    2    2    1    0    0    0
    0    0    0    

    2    2    1    1 8431]
0
suitcase
[  29    0    0    0    0    0    0    0    2    0    1    0    2    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 8432]
1
suitcase
[  29    1    1    2    0    0    0    1    2    0    0    1    2    1
    1    0    0    2    1    2    0    0    0    0    1    0    1    1
    2    2    1    1 8433]
2
suitcase
[  29    0    0    0    3    2    2    1    2    2    1    1    0    0
    1    2    1    0    0    0    0    0    0    0    1    0    0    0
    0    0    0    1 8436]
2
suitcase
[  29    0    0    0    0    0    0    0    2    2    0    0    0    0
    0    0    0    2    0    0    0    0    0    0    1    0    0    1
    2    0    1    1 8439]
1
suitcase
[  29    0    0    0    3    2    2    0    2    0    0    1    2    0
    0    0    1    0    1    2    0    0    2    1    1    0    0    0
    2    2    1    1 8440]
2
book
[  74    0    0    0    0    0    0    0    2    0    1    1    2 

...

clock
[   75     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     1     0     0     0     2     2     0     1 33169]
0
dining table
[   61     1     0     0     0     0     0     0     0     0     0     0
     2     0     0     0     0     0     0     0     0     0     0     0
     1     0     1     1     2     2     1     1 33170]
0
suitcase
[   29     1     0     0     3     2     0     0     0     0     0     0
     0     0     0     0     1     0     0     0     0     0     0     0
     1     0     1     1     2     2     1     1 33173]
0
suitcase
[   29     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     1     0     0     0     2     2     1     1 33174]
0
dining table
[   61     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     1     0     0     0     0     0 

     1     0     0     0     2     2     0     0 34120]
0
clock
[   75     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     3     0     0 34123]
1
clock
[   75     0     0     0     0     0     0     1     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     2     0
     0     1     0     0     0     0     0     0 34125]
1
clock
[   75     0     0     0     3     2     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     1     1 34129]
0
suitcase
[   29     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0 34132]
1
clock
[   75     0     0     0     3     2     0     0     0     0     0     0
     0     0     0  

     1     0     0     0     2     2     1     1 35013]
0
clock
[   75     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     2     1     1 35014]
1
suitcase
[   29     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     1     0     0     0     0     0     0     0
     1     0     0     0     0     2     1     0 35015]
1
clock
[   75     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     2     0     1     1 35016]
1
dining table
[   61     0     0     0     3     2     0     0     0     0     0     0
     0     0     0     0     1     0     0     0     0     0     0     0
     1     0     0     0     2     2     1     1 35017]
0
clock
[   75     0     0     0     3     2     0     0     0     0     0     0
     0     0 

     0     0     1     1     0     0     0     0 36010]
1
suitcase
[   29     0     0     2     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     1     0     0     1     0 36011]
1
clock
[   75     1     1     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     2     0     0 36013]
1
clock
[   75     1     0     2     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     1     1     0     0     0     0 36014]
1
clock
[   75     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     2     2     0     0     1     0 36015]
1
clock
[   75     1     1     0     0     0     0     0     0     0     0     0
     0     0     0  

1
clock
[   75     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     1     1     0     0     0     0 36989]
1
suitcase
[   29     1     0     2     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     1     1     0     0     0     0 36990]
1
handbag
[   27     1     0     0     0     0     0     0     0     0     0     1
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     1     0     0     0     0     0 36991]
1
suitcase
[   29     0     0     0     0     0     0     0     0     0     0     1
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     1     0     0     0     0     0 36994]
1
book
[   74     1     0     2     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0

In [137]:
len(points3D_on_images)

16542

In [133]:
points3D_on_images_sorted = np.sort(points3D_on_images, axis=0)  
for a in points3D_on_images_sorted:
    print(class_names[a[0]])
    print(a)
    

handbag
[27  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  1]
handbag
[27  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  2]
handbag
[27  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  6]
handbag
[27  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  8]
handbag
[27  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  9]
handbag
[27  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0 10]
handbag
[27  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0 11]
handbag
[27  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0 13]
handbag
[27  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0 14]
handbag
[2

    0    0    0    0 1199]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 1201]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 1202]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 1204]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 1205]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 1207]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
   

    0    0    0    0 2850]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 2851]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 2853]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 2855]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 2858]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 2859]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
   

suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 6732]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 6736]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 6738]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 6742]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 6747]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0

    0    0    0    0 9452]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 9460]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 9467]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 9469]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 9472]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0 9484]
suitcase
[  29    0    0    0    0    0    0    0    0    0    0    0    0    0
   

...

     1     0     0     1     2     2     1     1 31726]
book
[   74     0     0     0     0     0     0     0     0     0     0     1
     2     0     0     0     0     0     0     0     0     0     0     1
     1     0     0     1     2     2     1     1 31728]
book
[   74     0     0     0     0     0     0     0     0     0     0     1
     2     0     0     0     0     0     0     0     0     0     0     1
     1     0     0     1     2     2     1     1 31729]
book
[   74     0     0     0     0     0     0     0     0     0     0     1
     2     0     0     0     0     0     0     0     0     0     0     1
     1     0     0     1     2     2     1     1 31730]
book
[   74     0     0     0     0     0     0     0     0     0     0     1
     2     0     0     0     0     0     0     0     0     0     0     1
     1     0     0     1     2     2     1     1 31731]
book
[   74     0     0     0     0     0     0     0     0     0     0     1
     2     0     0     0     0     0  

     1     0     0     1     2     2     1     1 33127]
book
[   74     0     0     0     0     2     0     0     0     0     0     1
     2     1     1     0     1     2     0     1     1     0     2     1
     1     0     0     1     2     2     1     1 33129]
book
[   74     0     0     0     0     2     0     0     0     0     0     1
     2     1     1     0     1     2     0     1     1     0     2     1
     1     0     0     1     2     2     1     1 33130]
book
[   74     0     0     0     0     2     0     0     0     0     0     1
     2     1     1     0     1     2     0     1     1     0     2     1
     1     0     0     1     2     2     1     1 33133]
book
[   74     0     0     0     0     2     0     0     0     0     0     1
     2     1     1     0     1     2     0     1     1     0     2     1
     1     0     0     1     2     2     1     1 33134]
book
[   74     0     0     0     0     2     0     0     0     0     0     1
     2     1     1     0     1     2  

     1     1     1     1     2     2     1     1 34522]
clock
[   75     0     1     2     3     2     2     1     2     2     1     1
     2     1     1     2     1     2     1     2     1     0     2     1
     1     1     1     1     2     2     1     1 34523]
clock
[   75     0     1     2     3     2     2     1     2     2     1     1
     2     1     1     2     1     2     1     2     1     0     2     1
     1     1     1     1     2     2     1     1 34524]
clock
[   75     0     1     2     3     2     2     1     2     2     1     1
     2     1     1     2     1     2     1     2     1     0     2     1
     1     1     1     1     2     2     1     1 34527]
clock
[   75     0     1     2     3     2     2     1     2     2     1     1
     2     1     1     2     1     2     1     2     1     0     2     1
     1     1     1     1     2     2     1     1 34528]
clock
[   75     0     1     2     3     2     2     1     2     2     1     1
     2     1     1     2     1   

     1     1     1     1     2     2     1     1 35749]
clock
[   75     1     1     2     3     2     2     1     2     2     1     1
     2     1     1     2     1     2     1     2     1     1     2     1
     1     1     1     1     2     2     1     1 35750]
clock
[   75     1     1     2     3     2     2     1     2     2     1     1
     2     1     1     2     1     2     1     2     1     1     2     1
     1     1     1     1     2     2     1     1 35751]
clock
[   75     1     1     2     3     2     2     1     2     2     1     1
     2     1     1     2     1     2     1     2     1     1     2     1
     1     1     1     1     2     2     1     1 35753]
clock
[   75     1     1     2     3     2     2     1     2     2     1     1
     2     1     1     2     1     2     1     2     1     1     2     1
     1     1     1     1     2     2     1     1 35754]
clock
[   75     1     1     2     3     2     2     1     2     2     1     1
     2     1     1     2     1   

     1     1     1     1     2     2     1     1 36944]
clock
[   75     1     1     2     3     2     2     1     2     2     1     1
     2     1     1     2     1     2     1     2     2     1     2     1
     1     1     1     1     2     2     1     1 36950]
clock
[   75     1     1     2     3     2     2     1     2     2     1     1
     2     1     1     2     1     2     1     2     2     1     2     1
     1     1     1     1     2     2     1     1 36954]
clock
[   75     1     1     2     3     2     2     1     2     2     1     1
     2     1     1     2     1     2     1     2     2     1     2     1
     1     1     1     1     2     2     1     1 36955]
clock
[   75     1     1     2     3     2     2     1     2     2     1     1
     2     1     1     2     1     2     1     2     2     1     2     1
     1     1     1     1     2     2     1     1 36956]
clock
[   75     1     1     2     3     2     2     1     2     2     1     1
     2     1     1     2     1   

In [40]:
max(points3D)

37747

In [ ]:
for a in mask:
    for b in a:
        if b != 0 and b != 2 and b != 1:
            print(b)